# EXPLORATORY ANALYSIS - DATA PROCESSING

In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import os
import nltk
from IPython.display import HTML

os.chdir("C:\\Users\\ffitzpatrick\\Desktop\\Documents perso\\0. Perso\\Clinical trials - project\\1. Data\\1. Audit and cleaning\\Final database reduced")

#CT=pd.read_csv('CT_final.csv',encoding='latin-1')

In [3]:
os.getcwd()

'C:\\Users\\ffitzpatrick\\Desktop\\Documents perso\\0. Perso\\Clinical trials - project\\1. Data\\1. Audit and cleaning\\Final database reduced'

In [2]:
def View(df):
    css = """<style>
    table { border-collapse: collapse; border: 3px solid #eee; }
    table tr th:first-child { background-color: #eeeeee; color: #333; font-weight: bold }
    table thead th { background-color: #eee; color: #000; }
    tr, th, td { border: 1px solid #ccc; border-width: 1px 0 0 1px; border-collapse: collapse;
    padding: 3px; font-family: monospace; font-size: 10px }</style>
    """
    s  = '<script type="text/Javascript">'
    s += 'var win = window.open("", "Title", "toolbar=no, location=no, directories=no, status=no, menubar=no, scrollbars=yes, resizable=yes, width=780, height=200, top="+(screen.height-400)+", left="+(screen.width-840));'
    s += 'win.document.body.innerHTML = \'' + (df.to_html() + css).replace("\n",'\\').replace("'","") + '\';'
    s += '</script>'

    return(HTML(s+css))

In [4]:
CTred=pd.read_csv('CT_clean.csv',encoding='latin-1')


C:\Users\ffitzpatrick\AppData\Local\Continuum\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:2717: DtypeWarning: Columns (23,24,38,58,62,70,71,72,103,105,111,114,115,116,117,118,127,128) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [5]:
View(CTred.head(500))

In [142]:
View(pd.DataFrame(CTred.columns.values))

In [131]:
#test
CTred.iloc[37:39,60:63]
CTred.iloc[0:5,]

intervention_browse.comment  \
0                                                NaN   
1                                                NaN   
2  CAUTION:  The following MeSH terms are assigne...   
3                                                NaN   
4                                                NaN   

                 intervention_browse.mesh_term  
0                                          NaN  
1                                          NaN  
2  Keyhole-limpet hemocyanin|Freund's Adjuvant  
3                                          NaN  
4                                          NaN

In [8]:
CTred['Nb non missing values'] = CTred.apply(lambda x: x.count(), axis=1)
CTred["Nb non missing values"].idxmax()

239136

In [35]:
View(CTred.loc[1:1000,:])

##    BUILDING THE DATABASE

In [399]:
#len(CTred.loc[:,"acronym.text"].unique())
#CTred[["acronym.text","arm_group.arm_group_label"]].apply(lambda x: np.unique(x).size)
#CT.apply(lambda x: len(x.unique()))
CTsummary=pd.DataFrame(CT.apply(lambda x: x.isnull().sum()),columns=["Nb Missing Values"])
CTsummary["Nb Unique Values"]=CT.apply(lambda x: len(x.unique()))
CTsummary["Multiple text Variable"]=CT.apply(lambda x: x.str.contains('[|]').any())
CTsummary["Number of Multiple text"]=CT.apply(lambda x: len(CT[x.str.contains('[|]')==True]))
CTsummary.head()

Nb Missing Values  Nb Unique Values  \
Unnamed: 0                                 0            239623   
acronym.text                          181251             47646   
arm_group.arm_group_label              43802            147763   
arm_group.arm_group_type               72423              1583   
arm_group.description                  74575            161789   

                          Multiple text Variable  Number of Multiple text  
Unnamed: 0                                 False                        0  
acronym.text                                True                        1  
arm_group.arm_group_label                   True                   136638  
arm_group.arm_group_type                    True                   123086  
arm_group.description                       True                   115845

In [400]:
#CTsummary.to_csv("CT_summary.csv")
CTsummary.to_csv("C:\\Users\\ffitzpatrick\\Desktop\\Documents perso\\Perso\\Clinical trials - project\\2. Analysis\\Analysis extract\\CT_summary.csv")

In [398]:
#CTsummary.head(20)
CT.loc[:,"acronym.text"].str.contains('[|]').any()
CT.loc[:,"acronym.text"].str.contains('[|]').value_counts()
len(CT[CT.loc[:,"acronym.text"].str.contains('[|]')==True])

1

In [5]:
CTred=CT.drop("Unnamed: 0",axis=1)
#CTred=CTred.drop(0,axis=0)

### Reformating Numerical variables

In [6]:
CTred[["enrollment.text"]].dtypes
CTred["enrollment"]=pd.to_numeric(CTred.loc[:,"enrollment.text"],errors='coerce')
CTred.loc[1:5,"enrollment"]

1      NaN
2    112.0
3      NaN
4      NaN
5      NaN
Name: enrollment, dtype: float64

In [7]:
CTred["number_of_arms"]=pd.to_numeric(CTred.loc[:,"number_of_arms.text"],errors='coerce')
CTred["number_of_groups"]=pd.to_numeric(CTred.loc[:,"number_of_groups.text"],errors='coerce')
CTred.loc[1:5,"number_of_arms"]

1   NaN
2   NaN
3   NaN
4   NaN
5   NaN
Name: number_of_arms, dtype: float64

In [8]:
dictionary_unit={"Years":1,"Year":1,"Months":1/12,"Month":1/12, 
                 "Weeks":1/52,"Week":1/52,"Days":1/365,"Day":1/365,"Hours":1/(365/24),"Hour":1/(365/24),"Minutes":1/(365/24/60),"Minute":1/(365/24/60)}


In [138]:
CTred['MInimum_age_num'], CTred['Minimum_age_unit'] = CTred['eligibility.minimum_age'].str.split(' ', 1).str
CTred['Minimum_age_unit_2']=CTred['Minimum_age_unit'].replace(dictionary_unit)
CTred['MInimum_age_num_2']=pd.to_numeric(CTred.loc[:,'MInimum_age_num'],errors='coerce')
CTred["Minimum_age"]=CTred["MInimum_age_num_2"]*CTred["Minimum_age_unit_2"]

CTred[['eligibility.minimum_age',"MInimum_age_num","Minimum_age_unit","Minimum_age_unit_2","MInimum_age_num_2","Minimum_age"]][100:180]
CTred=CTred.drop(["MInimum_age_num","Minimum_age_unit","Minimum_age_unit_2","MInimum_age_num_2"],axis=1)

In [13]:
CTred['Maximum_age_num'], CTred['Maximum_age_unit'] = CTred['eligibility.maximum_age'].str.split(' ', 1).str
CTred['Maximum_age_unit_2']=CTred['Maximum_age_unit'].replace(dictionary_unit)
CTred['Maximum_age_num_2']=pd.to_numeric(CTred.loc[:,'Maximum_age_num'],errors='coerce')
CTred["Maximum_age"]=CTred["Maximum_age_num_2"]*CTred["Maximum_age_unit_2"]

CTred[['eligibility.maximum_age',"Maximum_age_num","Maximum_age_unit","Maximum_age_unit_2","Maximum_age_num_2","Maximum_age"]][100:180]
CTred=CTred.drop(["Maximum_age_num","Maximum_age_unit","Maximum_age_unit_2","Maximum_age_num_2"],axis=1)

In [147]:
CTred['Target_duration_num'], CTred['Target_duration_unit'] = CTred['target_duration.text'].str.split(' ', 1).str
CTred['Target_duration_unit_2']=CTred['Target_duration_unit'].replace(dictionary_unit)
CTred['Target_duration_num_2']=pd.to_numeric(CTred.loc[:,'Target_duration_num'],errors='coerce')
CTred["Target_duration"]=CTred["Target_duration_num_2"]*CTred["Target_duration_unit_2"]

CTred[['target_duration.text',"Target_duration_num","Target_duration_unit","Target_duration_unit_2","Target_duration_num_2","Target_duration"]].dropna(thresh=2)[1:180]
CTred=CTred.drop(["Target_duration_num","Target_duration_unit","Target_duration_unit_2","Target_duration_num_2"],axis=1)

In [163]:
CTred[["target_duration.text","Target_duration"]].dropna()

target_duration.text  Target_duration
2439                 1 Day         0.002740
2732               3 Years         3.000000
2759               4 Weeks         0.076923
3569              15 Years        15.000000
3895               90 Days         0.246575
4232               2 Years         2.000000
4394               5 Years         5.000000
4850             12 Months         1.000000
5155              12 Weeks         0.230769
5167               9 Years         9.000000
5176               2 Years         2.000000
7818              99 Years        99.000000
8356                1 Year         1.000000
9119             12 Months         1.000000
9172             12 Months         1.000000
9616                1 Year         1.000000
12138              3 Years         3.000000
12303               1 Year         1.000000
12832             6 Months         0.500000
12905             15 Years        15.000000
13809            12 Months         1.000000
14455               8 Days         0.021918
14790             10 Years        10.000000
14837              3 Years         3.000000
16169              5 Years         5.000000
16331               1 Year         1.000000
16379              2 Weeks         0.038462
17721             10 Years        10.000000
18537              3 Years         3.000000
18760              4 Years         4.000000
...                    ...              ...
55688              5 Years         5.000000
55725             10 Years        10.000000
55817            24 Months         2.000000
55849              3 Years         3.000000
55863                1 Day         0.002740
55873              5 Years         5.000000
55901              2 Years         2.000000
55903              2 Years         2.000000
55976              1 Month         0.083333
55980             6 Months         0.500000
55987              3 Years         3.000000
56000               3 Days         0.008219
56033               1 Year         1.000000
56044                1 Day         0.002740
56057             6 Months         0.500000
56078               1 Year         1.000000
56082               1 Year         1.000000
56113             6 Months         0.500000
56136              1 Month         0.083333
56171                1 Day         0.002740
56205               7 Days         0.019178
56221              5 Years         5.000000
56225             3 Months         0.250000
56249               1 Year         1.000000
56270               2 Days         0.005479
56298             9 Months         0.750000
56322               5 Days         0.013699
56331              5 Years         5.000000
56387              1 Month         0.083333
56413            18 Months         1.500000

[1021 rows x 2 columns]

### Reformating dates variables

In [148]:
Var_dates=[col for col in CTred.columns.values if "date" in col]
Var_dates.remove("required_header.download_date")

CTred.dtypes
CTred[Var_dates].dtypes
CTred[Var_dates].head(10)

completion_date.text firstreceived_date.text  \
0                  NaN        November 3, 1999   
1                  NaN        November 3, 1999   
2           March 2012        November 3, 1999   
3                  NaN        January 18, 2000   
4                  NaN        January 18, 2000   
5                  NaN        January 18, 2000   
6                  NaN        January 18, 2000   
7                  NaN        January 18, 2000   
8                  NaN        January 18, 2000   
9       September 2013      September 23, 1999   

  firstreceived_results_date.text firstreceived_results_disposition_date.text  \
0                             NaN                                         NaN   
1                             NaN                                         NaN   
2                             NaN                                         NaN   
3                             NaN                                         NaN   
4                             NaN                                         NaN   
5                             NaN                                         NaN   
6                             NaN                                         NaN   
7                             NaN                                         NaN   
8                             NaN                                         NaN   
9                             NaN                                         NaN   

  lastchanged_date.text primary_completion_date.text start_date.text  \
0         June 23, 2005                          NaN             NaN   
1         June 23, 2005                          NaN             NaN   
2      November 6, 2012                   March 2012       July 2002   
3         June 23, 2005                          NaN             NaN   
4         June 23, 2005                          NaN             NaN   
5         June 23, 2005                          NaN             NaN   
6         June 23, 2005                          NaN             NaN   
7         June 23, 2005                          NaN             NaN   
8         June 23, 2005                          NaN             NaN   
9        April 14, 2016                 October 2001  September 1997   

  verification_date.text  
0          December 2003  
1          December 2003  
2          November 2012  
3          November 2000  
4          December 2003  
5          December 2003  
6          December 2003  
7         September 2000  
8          December 2003  
9             April 2016

In [149]:
Var_dates_new=[x.replace(".text","") for x in Var_dates]
CTred[Var_dates_new]=CTred[Var_dates].apply(pd.to_datetime,axis=0)
#=pd.to_datetime(CTred[Var_dates])

In [119]:
CTred[Var_dates_new].head()

completion_date firstreceived_date firstreceived_results_date  \
1      2013-01-01         2011-10-31                        NaT   
2      2010-12-01         2011-10-27                        NaT   
3      2013-10-01         2011-10-31                        NaT   
4             NaT         2011-10-31                        NaT   
5      2014-12-01         2011-09-09                        NaT   

  firstreceived_results_disposition_date lastchanged_date  \
1                                    NaT       2013-01-22   
2                                    NaT       2011-10-31   
3                                    NaT       2014-04-09   
4                                    NaT       2017-01-30   
5                                    NaT       2015-01-21   

  primary_completion_date start_date verification_date  
1              2011-12-01 2008-05-01        2013-01-01  
2              2010-11-01 2006-01-01        2011-10-01  
3              2012-05-01 2011-05-01        2014-04-01  
4                     NaT        NaT        2017-01-01  
5              2013-12-01 2011-09-01        2015-01-01

### Reformating text structured variables

#### Intro

In [199]:
import nltk
import re
from collections import Counter
from nltk.corpus import stopwords

In [309]:
#Check which variables is composed of several other variables
#True in CTred.loc[:,"intervention.arm_group_label"].str.contains('[|]').values
CTred.loc[:,"location.facility"].str.contains('[|]').any()

True

#### Arm Group Type

In [253]:
CTred['tokenized_arm_type']=CTred['arm_group.arm_group_type'].str.lower()
CTred['tokenized_arm_type']=CTred['tokenized_arm_type'].str.replace(', ', '|').str.split("|").tolist()
CTred.loc[1:20,'tokenized_arm_type']

1                                   NaN
2                                   NaN
3                                   NaN
4                                   NaN
5                                   NaN
6                                   NaN
7                                   NaN
8                                   NaN
9     [experimental, active comparator]
10                                  NaN
11                                  NaN
12                                  NaN
13                                  NaN
14                                  NaN
15                                  NaN
16                                  NaN
17                                  NaN
18                                  NaN
19                                  NaN
20                                  NaN
Name: tokenized_arm_type, dtype: object

In [254]:
armtype_count = Counter(CTred['tokenized_arm_type'].apply(pd.Series).stack())
armtype_count.most_common(10)

[('experimental', 193389),
 ('active comparator', 85269),
 ('placebo comparator', 37992),
 ('no intervention', 17080),
 ('other', 16715),
 ('sham comparator', 3488),
 ('case', 30),
 ('control', 17),
 ('treatment comparison', 2)]

#### Condition.text

In [ ]:
CTred['tokenized_conditions']=CTred['condition.text'].str.lower()
CTred['tokenized_conditions']=CTred['tokenized_conditions'].str.replace(', ', '|').str.split("|").tolist()
CTred.loc[4,'tokenized_conditions']
CTred[["condition.text","tokenized_conditions"]][1:20]

In [241]:
count = Counter(CTred['tokenized_conditions'].apply(pd.Series).stack())

Condition  count
0                       lead poisoning     19
1                               cancer   1737
2                   rheumatic diseases     34
3                        heart defects     59
4                           congenital     94
5              cardiovascular diseases   1371
6                     coronary disease    591
7                              obesity   3959
8                       mouth diseases     15
9                  glucose intolerance     65
10                            diabetes   2046
11                acanthosis nigricans      5
12                              myopia    371
13                retinitis pigmentosa     92
14                       macular edema    156
15                             cystoid      9
16                      optic neuritis     32
17                      hiv infections   3034
18  acquired immunodeficiency syndrome    138
19           cytomegalovirus retinitis     60
20                            cataract    405
21                             uveitis    153
22                chlamydia infections     18
23               ophthalmia neonatorum      1
24                           esotropia      9
25                            glaucoma    679
26                         astigmatism    116
27                   choroid neoplasms      2
28                 ocular hypertension    388
29           ischemic optic neuropathy      7
..                                 ...    ...
70       substance withdrawal syndrome     22
71           alcohol-related disorders     48
72                       shcizophrenia      1
73                tobacco use disorder    218
74       amphetamine-related disorders     30
75                             vertigo     33
76                        hearing loss    189
77                       sensorineural     10
78                           pneumonia    501
79                          aspiration     24
80                        otitis media     72
81                          depression   2107
82                      panic disorder    126
83                         agoraphobia     21
84                    bipolar disorder    783
85                    phobic disorders     20
86                       social phobia     66
87             public speaking anxiety      1
88                       schizophrenia   1985
89       obsessive-compulsive disorder    143
90           major depressive disorder    858
91                   anxiety disorders    212
92               personality disorders     26
93           drug-resistant depression      1
94                         melancholia      3
95                    stress disorders    197
96                      post-traumatic    166
97                     sleep disorders    155
98                         child abuse     37
99                    conduct disorder     48

[100 rows x 2 columns]

In [249]:
cond_count_df = pd.DataFrame.from_dict(count, orient='index').reset_index()
cond_count_df = count_df.rename(index=str,columns={"index":'Condition', 0:'count'})
cond_count_df.head(100)
cond_count_df.sort("count",ascending=False)

C:\Users\ffitzpatrick\AppData\Local\Continuum\Anaconda3\lib\site-packages\ipykernel\__main__.py:4: FutureWarning: sort(columns=....) is deprecated, use sort_values(by=.....)


Condition  count
294                                              healthy   6145
473                                        breast cancer   4467
7                                                obesity   3959
54                                     diabetes mellitus   3700
17                                        hiv infections   3034
149                                         hypertension   2796
550                                                 pain   2703
206                                               asthma   2486
704                                      prostate cancer   2359
277                                             lymphoma   2164
81                                            depression   2107
10                                              diabetes   2046
88                                         schizophrenia   1985
232                                             leukemia   1954
1714                             coronary artery disease   1947
163                                        heart failure   1854
1593                                              stroke   1819
1                                                 cancer   1737
869                                          lung cancer   1721
262                                               type 2   1699
868                                    colorectal cancer   1616
106                                 rheumatoid arthritis   1555
112                                       osteoarthritis   1494
5                                cardiovascular diseases   1371
3933                                     type 2 diabetes   1317
745                                     multiple myeloma   1261
2524                            type 2 diabetes mellitus   1249
540                                                  hiv   1226
645                                            carcinoma   1219
175                                  atrial fibrillation   1197
...                                                  ...    ...
28755                              ewing's family tumors      1
28757  supra-tentorial primative neuro-ectodermal tum...      1
28758           atypical teratoid/rhabdoid tumor (at/rt)      1
28759                            proprioceptive training      1
28761          irritable bowel syndrome without diarrhea      1
28764                 severe hemophilia a with inhibitor      1
28767                             apgar; 0-3 at 1 minute      1
28768                                       birth-weight      1
28740                                    unspecified use      1
28736      change in corneal endothelial cell morphology      1
28708                               knee joint arthritis      1
28735                                   iol implantation      1
28709                            knee joint arthroplasty      1
28710                                antimuscarinic drug      1
28711                               alveolar bone losses      1
28712              preterm premature rupture of membrane      1
28713  influence of genotype of drug metabolizing enz...      1
28714  influence of aspirin on the pharmacokinetics/p...      1
28716                   postoperative residual paralysis      1
28717                                   financial burden      1
28718                                     lung diffusion      1
28723                               irvine gass syndrome      1
28724  gastric adenocarcinoma with peritoneal carcino...      1
28725  siewert type ii adenocarcinoma of esophagogast...      1
28726  siewert type iii adenocarcinoma of esophagogas...      1
28727                                        alcoholism,      1
28728                    prophylaxis of lyme borreliosis      1
28729                          radiation induced sarcoma      1
28734                        congenital cataract surgery      1
59627                                       bladder care      1

[59628 rows x 2 columns]

In [257]:
count.most_common(20)

[('healthy', 6145),
 ('breast cancer', 4467),
 ('obesity', 3959),
 ('diabetes mellitus', 3700),
 ('hiv infections', 3034),
 ('hypertension', 2796),
 ('pain', 2703),
 ('asthma', 2486),
 ('prostate cancer', 2359),
 ('lymphoma', 2164),
 ('depression', 2107),
 ('diabetes', 2046),
 ('schizophrenia', 1985),
 ('leukemia', 1954),
 ('coronary artery disease', 1947),
 ('heart failure', 1854),
 ('stroke', 1819),
 ('cancer', 1737),
 ('lung cancer', 1721),
 ('type 2', 1699)]

In [ ]:
View(count_df.head(1000))

#### Condition Mesh

In [255]:
CTred['tokenized_conditions_mesh']=CTred['condition_browse.mesh_term'].str.lower()
CTred['tokenized_conditions_mesh']=CTred['tokenized_conditions_mesh'].str.replace(', ', '|').str.split("|").tolist()
CTred.loc[1:10,'tokenized_conditions_mesh']

1                           [poisoning, lead poisoning]
2                                                   NaN
3               [rheumatic diseases, collagen diseases]
4     [heart diseases, congenital abnormalities, hea...
5     [cardiovascular diseases, coronary disease, co...
6                                                   NaN
7                                      [mouth diseases]
8           [glucose intolerance, acanthosis nigricans]
9                                              [myopia]
10                    [retinitis, retinitis pigmentosa]
Name: tokenized_conditions_mesh, dtype: object

In [256]:
cond_mesh_count = Counter(CTred['tokenized_conditions_mesh'].apply(pd.Series).stack())
cond_mesh_count.most_common(20)

[('diabetes mellitus', 13715),
 ('leukemia', 12543),
 ('carcinoma', 11739),
 ('lymphoma', 9012),
 ('chronic', 7855),
 ('breast neoplasms', 5791),
 ('neoplasms', 5676),
 ('syndrome', 5242),
 ('type 2', 4763),
 ('lung diseases', 4751),
 ('arthritis', 4480),
 ('depressive disorder', 4470),
 ('hiv infections', 4170),
 ('hypertension', 4156),
 ('lung neoplasms', 3958),
 ('disease', 3898),
 ('myeloid', 3864),
 ('hepatitis', 3778),
 ('osteoarthritis', 3739),
 ('depression', 3689)]

#### Eligibility simple criteria

In [430]:
eligibility_gender_count=CTred.loc[:,'eligibility.gender'].value_counts().sort_values(ascending=False)
#eligibility_gender_count.to_frame(name=["eligibility_gender Val","eligibility_gender Vol"]).reset_index()
eligibility_healthy_count=CTred.loc[:,'eligibility.healthy_volunteers'].value_counts().sort_values(ascending=False)
eligibility_sampling_count=CTred.loc[:,'eligibility.sampling_method'].value_counts().sort_values(ascending=False)
exp_access_count=CTred.loc[:,'has_expanded_access.text'].value_counts().sort_values(ascending=False)

No                            179502
Accepts Healthy Volunteers     57455
Name: eligibility.healthy_volunteers, dtype: int64

#### Intervention type

In [258]:
CTred['tokenized_intervention_type']=CTred['intervention.intervention_type'].str.lower()
CTred['tokenized_intervention_type']=CTred['tokenized_intervention_type'].str.replace(', ', '|').str.split("|").tolist()
CTred.loc[1:20,'tokenized_intervention_type']

1                                    [procedure]
2     [biological, biological, drug, biological]
3                                       [device]
4                                            NaN
5                                   [behavioral]
6                              [procedure, drug]
7                                    [procedure]
8                                            NaN
9                                 [other, other]
10                                  [drug, drug]
11                                        [drug]
12                                  [drug, drug]
13                                        [drug]
14                                      [device]
15                                      [device]
16                                  [drug, drug]
17                                      [device]
18                                        [drug]
19                              [device, device]
20                        [procedure, procedure]
Name: tokenized_inte

In [259]:
interventiontype_count = Counter(CTred['tokenized_intervention_type'].apply(pd.Series).stack())
interventiontype_count.most_common(10)

[('drug', 216987),
 ('other', 52303),
 ('procedure', 36138),
 ('device', 35582),
 ('behavioral', 31556),
 ('biological', 23089),
 ('dietary supplement', 12217),
 ('radiation', 6425),
 ('genetic', 2530),
 ('diagnostic test', 243)]

#### Intervention MESH

In [260]:
CTred['tokenized_intervention_mesh']=CTred['intervention_browse.mesh_term'].str.lower()
CTred['tokenized_intervention_mesh']=CTred['tokenized_intervention_mesh'].str.replace(', ', '|').str.split("|").tolist()
CTred.loc[1:20,'tokenized_intervention_mesh']

1                                                   NaN
2        [keyhole-limpet hemocyanin, freund's adjuvant]
3                                                   NaN
4                                                   NaN
5                                                   NaN
6                                                   NaN
7                                                   NaN
8                                                   NaN
9                                                   NaN
10    [vitamins, vitamin a, vitamin e, tocopherols, ...
11                                      [acetazolamide]
12                                          [vitamin a]
13    [immunoglobulins, intravenous, gamma-globulins...
14                                                  NaN
15                           [calcium heparin, heparin]
16    [silver nitrate, erythromycin stearate, erythr...
17                                                  NaN
18                                       [fluoro

In [261]:
intervention_mesh_count = Counter(CTred['tokenized_intervention_mesh'].apply(pd.Series).stack())
intervention_mesh_count.most_common(20)

[('antibodies', 4977),
 ('insulin', 4918),
 ('vaccines', 4843),
 ('monoclonal', 2984),
 ('cyclophosphamide', 2458),
 ('paclitaxel', 2404),
 ('anesthetics', 2256),
 ('albumin-bound paclitaxel', 2233),
 ('cisplatin', 2150),
 ('vitamins', 2031),
 ('gemcitabine', 1847),
 ('carboplatin', 1842),
 ('globin zinc', 1830),
 ('dexamethasone', 1826),
 ('pharmaceutical solutions', 1816),
 ('bevacizumab', 1800),
 ('docetaxel', 1695),
 ('sirolimus', 1668),
 ('dexamethasone 21-phosphate', 1652),
 ('dexamethasone acetate', 1651)]

#### Keywords

In [263]:
CTred['tokenized_keyword']=CTred['keyword.text'].str.lower()
CTred['tokenized_keyword']=CTred['tokenized_keyword'].str.replace(', ', '|').str.split("|").tolist()
CTred.loc[1:20,'tokenized_keyword']

1                                     [lead overburden]
2                                                   NaN
3                                 [rheumatoid diseases]
4                   [cyanotic congenital heart disease]
5                                            [exercise]
6     [exercise, exertion, physical fitness, lipids,...
7                           [mouth mucosa, transplants]
8                                                   NaN
9                             [myopia, nearsightedness]
10          [retinitis pigmentosa, vitamin supplements]
11                                                  NaN
12                                                  NaN
13                                                  NaN
14                                                  NaN
15                                                  NaN
16                            [neonatal conjunctivitis]
17                                         [strabismus]
18                                              

In [264]:
keyword_count = Counter(CTred['tokenized_keyword'].apply(pd.Series).stack())
keyword_count.most_common(20)

[('pharmacokinetics', 2309),
 ('obesity', 2130),
 ('quality of life', 2078),
 ('pain', 2054),
 ('safety', 2044),
 ('breast cancer', 2038),
 ('cancer', 1990),
 ('depression', 1857),
 ('children', 1705),
 ('hiv', 1701),
 ('diabetes', 1658),
 ('exercise', 1652),
 ('stroke', 1320),
 ('hypertension', 1275),
 ('asthma', 1221),
 ('schizophrenia', 1199),
 ('inflammation', 1101),
 ('copd', 1079),
 ('heart failure', 1075),
 ('treatment', 1058)]

#### Location countries

In [265]:
CTred['tokenized_countries']=CTred['location_countries.country'].str.lower()
CTred['tokenized_countries']=CTred['tokenized_countries'].str.replace(', ', '|').str.split("|").tolist()
CTred.loc[1:20,'tokenized_countries']

1     [united states]
2     [united states]
3     [united states]
4     [united states]
5     [united states]
6     [united states]
7                 NaN
8     [united states]
9     [united states]
10                NaN
11                NaN
12    [united states]
13    [united states]
14                NaN
15    [united states]
16                NaN
17                NaN
18                NaN
19                NaN
20                NaN
Name: tokenized_countries, dtype: object

In [266]:
countries_count = Counter(CTred['tokenized_countries'].apply(pd.Series).stack())
countries_count.most_common(20)

[('united states', 100346),
 ('france', 16870),
 ('canada', 16618),
 ('germany', 15540),
 ('united kingdom', 13164),
 ('italy', 9532),
 ('china', 9301),
 ('spain', 9211),
 ('republic of', 8012),
 ('korea', 7890),
 ('netherlands', 7342),
 ('belgium', 7139),
 ('israel', 6078),
 ('denmark', 6031),
 ('australia', 5561),
 ('brazil', 5528),
 ('switzerland', 4943),
 ('poland', 4921),
 ('taiwan', 4740),
 ('sweden', 4729)]

#### Number of arms and groups

In [432]:
number_arms_count=CTred.loc[:,'number_of_arms.text'].value_counts().sort_values(ascending=False)
number_groups_count=CTred.loc[:,'number_of_groups.text'].value_counts().sort_values(ascending=False)

#### Overall Status

In [311]:
CTred['tokenized_official_role']=CTred['overall_official.role'].str.lower()
CTred['tokenized_official_role']=CTred['tokenized_official_role'].str.replace(', ', '|').str.split("|").tolist()
CTred.loc[1:20,'tokenized_official_role']

1                               NaN
2          [principal investigator]
3                               NaN
4                               NaN
5                               NaN
6                               NaN
7                               NaN
8                               NaN
9     [study chair, study director]
10                              NaN
11                              NaN
12                    [study chair]
13                              NaN
14                              NaN
15                              NaN
16                              NaN
17                              NaN
18                              NaN
19                              NaN
20                              NaN
Name: tokenized_official_role, dtype: object

In [312]:
official_role_count = Counter(CTred['tokenized_official_role'].apply(pd.Series).stack())
official_role_count.most_common(20)

[('principal investigator', 173296),
 ('study director', 53000),
 ('study chair', 30367),
 ('sub-investigator', 19)]

In [438]:
overall_status_count=CTred.loc[:,'overall_status.text'].value_counts().sort_values(ascending=False)
oversight_dmc_count=CTred.loc[:,'oversight_info.has_dmc'].value_counts().sort_values(ascending=False)

#### Phase, source and design study

In [443]:
phase_count=CTred.loc[:,'phase.text'].value_counts().sort_values(ascending=False)
source_count=CTred.loc[:,'source.text'].value_counts().sort_values(ascending=False)

study_design_intermodel_count=CTred.loc[:,'study_design_info.intervention_model'].value_counts().sort_values(ascending=False)
study_design_masking_count=CTred.loc[:,'study_design_info.masking'].value_counts().sort_values(ascending=False)
study_design_purpose_count=CTred.loc[:,'study_design_info.primary_purpose'].value_counts().sort_values(ascending=False)
study_design_type_count=CTred.loc[:,'study_type.text'].value_counts().sort_values(ascending=False)

## BUILD KEY VARIABLES FREQUENCY 

In [444]:
#CT_keyvar=pd.DataFrame(armtype_count.most_common(100),columns=["arm_group_type Val","arm_group_type Vol"])
#CT["condition Val","condition Vol"]=count.most_common(100)
CT_keyvar=pd.concat([pd.DataFrame(armtype_count.most_common(1000),columns=["arm_group_type Val","arm_group_type Vol"]),
                     pd.DataFrame(count.most_common(1000),columns=["condition Val","condition Vol"]),
                    pd.DataFrame(cond_mesh_count.most_common(1000),columns=["condition MESH Val","condition MESH Vol"]),
                    
                     pd.DataFrame({'eligibility_gender Val':eligibility_gender_count.index, 'eligibility_gender Vol':eligibility_gender_count.values}),
                     pd.DataFrame({'eligibility_healthy Val':eligibility_healthy_count.index, 'eligibility_healthy Vol':eligibility_healthy_count.values}),
                     pd.DataFrame({'eligibility_sampling Val':eligibility_sampling_count.index, 'eligibility_sampling Vol':eligibility_sampling_count.values}),
                     pd.DataFrame({'exp_access Val':exp_access_count.index, 'exp_access Vol':exp_access_count.values}),
                    
                     pd.DataFrame(interventiontype_count.most_common(1000),columns=["intervention_type Val","intervention_type Vol"]),
                    pd.DataFrame(intervention_mesh_count.most_common(1000),columns=["intervention_type Val","intervention_type Vol"]),
                    pd.DataFrame(keyword_count.most_common(1000),columns=["keyword Val","keyword Vol"]),
                     pd.DataFrame(countries_count.most_common(1000),columns=["location_countries Val","location_countries Vol"]),
                    
                     pd.DataFrame({'number_arms Val':number_arms_count.index, 'number_arms Vol':number_arms_count.values}),
                     pd.DataFrame({'number_groups Val':number_groups_count.index, 'number_groups Vol':number_groups_count.values}),
                     
                     pd.DataFrame(official_role_count.most_common(1000),columns=["overall_official_role Val","overall_official_role Vol"]),
                    
                     pd.DataFrame({'overall_status Val':overall_status_count.index, 'overall_status Vol':overall_status_count.values}),
                     pd.DataFrame({'oversight_dmc Val':oversight_dmc_count.index, 'oversight_dmc Vol':oversight_dmc_count.values}),
                    pd.DataFrame({'phase Val':phase_count.index, 'phase Vol':phase_count.values}),
                     pd.DataFrame({'source Val':source_count.index, 'source Vol':source_count.values}),
                    pd.DataFrame({'study_design_intermodel Val':study_design_intermodel_count.index, 'study_design_intermodel Vol':study_design_intermodel_count.values}),
                     pd.DataFrame({'study_design_masking Val':study_design_masking_count.index, 'study_design_masking Vol':study_design_masking_count.values}),
                     pd.DataFrame({'study_design_purpose Val':study_design_purpose_count.index, 'study_design_purpose Vol':study_design_purpose_count.values}),
                     pd.DataFrame({'study_design_type Val':study_design_type_count.index, 'study_design_type Vol':study_design_type_count.values})
                    ], axis=1)
CT_keyvar.iloc[0:10,30:]

oversight_dmc Val  oversight_dmc Vol        phase Val  phase Vol  \
0                No           119103.0          Phase 2    36915.0   
1               Yes            75363.0          Phase 3    27319.0   
2               NaN                NaN          Phase 1    26197.0   
3               NaN                NaN          Phase 4    23428.0   
4               NaN                NaN  Phase 1/Phase 2     8802.0   
5               NaN                NaN  Phase 2/Phase 3     4455.0   
6               NaN                NaN    Early Phase 1     2012.0   
7               NaN                NaN              NaN        NaN   
8               NaN                NaN              NaN        NaN   
9               NaN                NaN              NaN        NaN   

                                          source Val  source Vol  \
0  National Institutes of Health Clinical Center ...        4081   
1                    National Cancer Institute (NCI)        3546   
2                                    GlaxoSmithKline        3165   
3                                           Novartis        2553   
4                                             Pfizer        2517   
5                                        AstraZeneca        2237   
6                          Merck Sharp & Dohme Corp.        1958   
7                        M.D. Anderson Cancer Center        1773   
8                               Boehringer Ingelheim        1672   
9                                             Sanofi        1637   

  study_design_intermodel Val  study_design_intermodel Vol  \
0         Parallel Assignment                     106942.0   
1     Single Group Assignment                      57445.0   
2        Crossover Assignment                      17280.0   
3        Factorial Assignment                       3189.0   
4       Sequential Assignment                         84.0   
5                         NaN                          NaN   
6                         NaN                          NaN   
7                         NaN                          NaN   
8                         NaN                          NaN   
9                         NaN                          NaN   

                            study_design_masking Val  \
0                                         Open Label   
1  Double Blind (Subject, Caregiver, Investigator...   
2               Double Blind (Subject, Investigator)   
3                                         No masking   
4                   Single Blind (Outcomes Assessor)   
5                             Single Blind (Subject)   
6                                       Double-Blind   
7    Double Blind (Subject, Caregiver, Investigator)   
8  Double Blind (Subject, Investigator, Outcomes ...   
9          Double Blind (Subject, Outcomes Assessor)   

   study_design_masking Vol         study_design_purpose Val  \
0                   93298.0                        Treatment   
1                   16733.0                       Prevention   
2                   12986.0                    Basic Science   
3                   12283.0                       Diagnostic   
4                    8393.0                  Supportive Care   
5                    7723.0         Health Services Research   
6                    6217.0                        Screening   
7                    5293.0                            Other   
8                    4527.0  Educational/Counseling/Training   
9                    3046.0               Device Feasibility   

   study_design_purpose Vol             study_design_type Val  \
0                  130875.0                    Interventional   
1                   19947.0                     Observational   
2                    8423.0  Observational [Patient Registry]   
3                    8156.0                   Expanded Access   
4                    7064.0                               NaN   
5                    3751.0                               NaN   
6                    1

In [445]:
#CT_keyvar.to_csv("CT_keyvar.csv")
CT_keyvar.to_csv("C:\\Users\\ffitzpatrick\\Desktop\\Documents perso\\Perso\\Clinical trials - project\\2. Analysis\\Analysis extract\\CT_keyvar.csv")

In [446]:
CTred.to_csv("CT_clean.csv")

In [7]:

CTred.columns.values

array(['Unnamed: 0', 'acronym.text', 'arm_group.arm_group_label',
       'arm_group.arm_group_type', 'arm_group.description',
       'biospec_descr.textblock', 'biospec_retention.text',
       'brief_summary.textblock', 'brief_title.text',
       'completion_date.text', 'condition.text',
       'condition_browse.comment', 'condition_browse.mesh_term',
       'detailed_description.textblock', 'eligibility.criteria',
       'eligibility.gender', 'eligibility.healthy_volunteers',
       'eligibility.maximum_age', 'eligibility.minimum_age',
       'eligibility.sampling_method', 'eligibility.study_pop',
       'enrollment.text', 'firstreceived_date.text',
       'firstreceived_results_date.text',
       'firstreceived_results_disposition_date.text',
       'has_expanded_access.text', 'id_info.nct_alias', 'id_info.nct_id',
       'id_info.org_study_id', 'id_info.secondary_id',
       'intervention.arm_group_label', 'intervention.description',
       'intervention.intervention_name', 'interve

In [8]:
#Test
CTred.columns.values
CTtest=CTred[["arm_group.arm_group_type","condition.text","condition_browse.mesh_term",'eligibility.criteria',
           'eligibility.gender','eligibility.healthy_volunteers','eligibility.sampling_method','has_expanded_access.text','id_info.nct_id','intervention.intervention_type',
           'intervention_browse.mesh_term','keyword.text','last_known_status.text','location.facility','location.status','location_countries.country',
        'other_outcome.description', 'other_outcome.measure','other_outcome.time_frame','overall_official.role',
       'overall_status.text','oversight_info.has_dmc','oversight_info.is_fda_regulated_device','oversight_info.is_fda_regulated_drug', 'oversight_info.is_ppsd',
       'oversight_info.is_unapproved_device','oversight_info.is_us_export','patient_data.sharing_ipd', 'phase.text','primary_outcome.description',
       'primary_outcome.measure', 'primary_outcome.time_frame','responsible_party.responsible_party_type','secondary_outcome.description', 'secondary_outcome.measure',
       'secondary_outcome.time_frame','study_design_info.allocation','study_design_info.intervention_model','study_design_info.masking',
       'study_design_info.observational_model','study_design_info.primary_purpose','study_design_info.time_perspective','study_type.text',
       'why_stopped.text', 'enrollment', 'completion_date','firstreceived_date', 'firstreceived_results_date','firstreceived_results_disposition_date', 'lastchanged_date',
       'primary_completion_date', 'start_date', 'verification_date','number_of_arms','number_of_groups','Minimum_age','Maximum_age',"Target_duration"]]

In [9]:
CTtest.to_csv("CT_clean2.csv")

# ANALYSIS DATABASE

In [2]:
CTsim=pd.read_csv('CT_simple.csv',encoding='latin-1')

In [8]:
#Get dataset of all clinical trial without phase
import datetime 
CTred['firstreceived_date'] = pd.to_datetime(CTred['firstreceived_date'])
CTphasena=CTred[pd.isnull(CTred["phase.text"])]
CTphasena=CTphasena[CTphasena['firstreceived_date'] > datetime.date(year=2016,month=1,day=1)]
CTphasena['id_info.nct_id'].head(10)
#CTphasena.head(1000).to_csv("CT_phase_na.csv")

205947    NCT02645721
205949    NCT02645747
205954    NCT02645812
205955    NCT02645825
205963    NCT02645929
205971    NCT02646033
205973    NCT02646059
205980    NCT02646150
205985    NCT02646215
205986    NCT02646228
Name: id_info.nct_id, dtype: object

In [4]:
CTsim=CTred[['enrollment','eligibility.gender','eligibility.healthy_volunteers',
             'eligibility.sampling_method','has_expanded_access.text','Minimum_age','Maximum_age',
             'overall_status.text','phase.text','study_design_info.allocation','study_design_info.intervention_model','study_design_info.masking',
             'study_design_info.observational_model','study_design_info.primary_purpose','study_type.text',
             'number_of_arms','number_of_groups',"Target_duration",]]

In [157]:
def f(row):
    if row['start_date_rank'] > row['firstreceived_date_rank']:
        val = row['firstreceived_date']
    else:
        val = row['start_date']
    return val

def g(row):
    if row['primary_completion_date_rank'] > row['completion_date_rank']:
        val = row['completion_date']
    else:
        val = row['primary_completion_date']
    return val

In [158]:
CTdates["beg_date"]=CTdates.apply(f, axis=1)
CTdates["end_date"]=CTdates.apply(g, axis=1)

C:\Users\ffitzpatrick\AppData\Local\Continuum\Anaconda3\lib\site-packages\ipykernel\__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':
C:\Users\ffitzpatrick\AppData\Local\Continuum\Anaconda3\lib\site-packages\ipykernel\__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app


In [163]:
CTsim=pd.concat([CTsim,CTdates[["beg_date","end_date"]]],axis=1)

In [34]:
CTsim['beg_date'] = pd.to_datetime(CTsim['beg_date'])
CTsim['end_date'] = pd.to_datetime(CTsim['end_date'])
CTsim["Duration"]=CTsim['end_date']-CTsim['beg_date']

In [173]:
CTsim["Duration_days"]=CTsim["Duration"].dt.days

In [35]:
CTsim['beg_date_year'] = CTsim['beg_date'].dt.year

In [10]:
CTsim.head()
CTsim.dtypes
#CTsim.columns.values

Unnamed: 0                                     int64
Unnamed: 0.1                                   int64
enrollment                                   float64
eligibility.gender                            object
eligibility.healthy_volunteers                object
eligibility.sampling_method                   object
has_expanded_access.text                      object
Minimum_age                                  float64
Maximum_age                                  float64
overall_status.text                           object
phase.text                                    object
study_design_info.allocation                  object
study_design_info.intervention_model          object
study_design_info.masking                     object
study_design_info.observational_model         object
study_design_info.primary_purpose             object
study_type.text                               object
number_of_arms                               float64
number_of_groups                             f

In [9]:
CTsim.to_csv("CT_simple.csv")

## Analysis of dates

In [131]:
CTdates=CTred[['completion_date','firstreceived_date', 'firstreceived_results_date','firstreceived_results_disposition_date', 'lastchanged_date',
       'primary_completion_date', 'start_date', 'verification_date']]
list(CTdates.columns.values)
dates_rank=[s + "_rank" for s in list(CTdates.columns.values)]
dates_rank

['completion_date_rank',
 'firstreceived_date_rank',
 'firstreceived_results_date_rank',
 'firstreceived_results_disposition_date_rank',
 'lastchanged_date_rank',
 'primary_completion_date_rank',
 'start_date_rank',
 'verification_date_rank']

In [ ]:
CTdates[dates_rank]=CTdates.apply(lambda x: x.rank(), axis=1)

In [145]:
dates_rank=CTdates[dates_rank].apply(lambda x: x.value_counts(dropna=False))
#dates_rank.to_csv("CT_dates_rank.csv")

ValueError: Must pass DataFrame with boolean values only

In [146]:
dates_rank.to_csv("C:\\Users\\ffitzpatrick\\Desktop\\Documents perso\\Perso\\Clinical trials - project\\2. Analysis\\Analysis extract\\CT_dates_rank.csv")

## Correlations enrollment and duration VS main categories

### Arm and intervention types reformating

In [5]:
CTsim['tokenized_intervention_type']=CTred['tokenized_intervention_type']
CTsim['tokenized_arm_type']=CTred['tokenized_arm_type']

In [6]:
CTtoken_intervention=CTsim['tokenized_intervention_type'].str.split(',', 2, expand=True)
CTsim["intervention_type_token_1"]=CTtoken_intervention.iloc[:,0].str.replace("[","")
CTsim["intervention_type_token_2"]=CTtoken_intervention.iloc[:,1].str.replace("]","")

In [7]:
CTtoken_arm=CTsim['tokenized_arm_type'].str.split(',', 2, expand=True)
CTsim["arm_type_token_1"]=CTtoken_arm.iloc[:,0].str.replace("[","")
CTsim["arm_type_token_2"]=CTtoken_arm.iloc[:,1].str.replace("]","")

In [99]:
#useful
CTsim["tokenized_intervention_type"].str.count(",").max(axis=0)

96.0

### Outputs reformating? 

In [8]:
CTred[['primary_outcome.description','primary_outcome.measure', 'primary_outcome.time_frame','secondary_outcome.description', 'secondary_outcome.measure','secondary_outcome.time_frame']]

primary_outcome.description  \
0                                                     NaN   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4                                                     NaN   
5                                                     NaN   
6                                                     NaN   
7                                                     NaN   
8                                                     NaN   
9                                                     NaN   
10                                                    NaN   
11                                                    NaN   
12                                                    NaN   
13                                                    NaN   
14                                                    NaN   
15                                                    NaN   
16                                                    NaN   
17                                                    NaN   
18                                                    NaN   
19                                                    NaN   
20                                                    NaN   
21      Comparison of the cumulative proportion of par...   
22                                                    NaN   
23                                                    NaN   
24                                                    NaN   
25                                                    NaN   
26                                                    NaN   
27                                                    NaN   
28                                                    NaN   
29                                                    NaN   
...                                                   ...   
239593  Recruitment rate|Percentage of participants wh...   
239594  Main effects of treatment and interaction betw...   
239595  fMRI based indices during emotional face proce...   
239596  Depression will be measured using tThe Persona...   
239597  The primary endpoint of the study is the numbe...   
239598  Diagnosis of recurrent and or untreated cervic...   
239599  Diary of Pain|Pressure Pain Threshold and Tole...   
239600  The Design Quality and Interface positively ra...   
239601  Z-scores are "pure numbers" (have no units of ...   
239602  Participation rate in screening colonoscopy fo...   
239603  IgG4 Antibodies against Eliminated Food Antige...   
239604  This will measure objective kidney disease kno...   
239605  Change in prevalence rate of chronic kidney di...   
239606  Patients will be subject to blood sample perio...   
239607  Overall survival in subjects with acute liver ...   
239608  Defined as an increase from baseline of â?¥ 3 ...   
239609                                 Clinical valuation   
239610  calculated as the proportion of patients with ...   
239611  The number of subjects develop to hepatocellul...   
239612  Compare AOFAS scores between AORIF versus ORIF...   
239613  Change in average well-being measured by 10 sc...   
239614  The specific endpoints for safety and reactoge...   
239615  Objective and self-reported|Objective and self...   
239616          Changes in urinary biomarkers of nicotine   
239617  Change in plasma vitamin D levels from baselin...   
239618  The AKE is performed using an experimental app...   
239619  Qualitative semi-structured interviews perform...   
239620  Rate of residual ischemia defined as iFR <0.90...   
239621  Safety measured by occurrence of study related...   
239622  the neuropsychological tests to measure cognit...   

                                  primary_outcome.measure  \
0                                                     NaN   
1                                                     NaN   
2       To assess whether patients can mediate an appr...   
3  

In [27]:
CTsim

Unnamed: 0  Unnamed: 0.1  enrollment eligibility.gender  \
0                0             0         NaN             Female   
1                1             1         NaN             Female   
2                2             2       112.0                All   
3                3             3         NaN                All   
4                4             4         NaN                All   
5                5             5         NaN             Female   
6                6             6         NaN                All   
7                7             7         NaN                All   
8                8             8         NaN                All   
9                9             9       469.0                All   
10              10            10         NaN                All   
11              11            11         NaN                All   
12              12            12         NaN                All   
13              13            13         NaN                All   
14              14            14         NaN                All   
15              15            15         NaN                All   
16              16            16         NaN                All   
17              17            17         NaN                All   
18              18            18         NaN                All   
19              19            19         NaN                All   
20              20            20         NaN                All   
21              21            21      1636.0                All   
22              22            22         NaN                All   
23              23            23         NaN                All   
24              24            24         NaN                All   
25              25            25         NaN                All   
26              26            26         NaN                All   
27              27            27         NaN                All   
28              28            28         NaN                All   
29              29            29         NaN                All   
...            ...           ...         ...                ...   
239593      239593        239593       100.0                All   
239594      239594        239594        80.0                All   
239595      239595        239595       105.0                All   
239596      239596        239596       120.0                All   
239597      239597        239597        50.0                All   
239598      239598        239598      1152.0             Female   
239599      239599        239599        45.0             Female   
239600      239600        239600        39.0                All   
239601      239601        239601       240.0             Female   
239602      239602        239602       168.0                All   
239603      239603        239603        70.0                All   
239604      239604        239604        50.0                All   
239605      239605        239605   2000000.0                All   
239606      239606        239606       200.0                All   
239607      239607        239607        16.0                All   
239608      239608        239608       300.0                All   
239609      239609        239609         1.0                All   
239610      239610        239610       608.0             Female   
239611      239611        239611       150.0                All   
239612      239612        239612        86.0                All   
239613      239613        239613        12.0               Male   
239614      239614        239614        15.0                All   
239615      239615        239615       120.0             Female   
239616      239616        239616       300.0                All   
239617      239617        239617        48.0                All   
239618      239618        239618        96.0                All   
239619      239619        239619         8.0             Female   
239620      239620        239620       500.0           

### Correlation calculations

In [18]:
cat_columns = CTsim.select_dtypes(['object']).columns
cat_columns=cat_columns.drop(['tokenized_intervention_type','tokenized_arm_type','beg_date','end_date', 'Duration'])

In [19]:
#cat_columns = CTsim.select_dtypes(['object']).columns
cat_columns_new=[s + "_cat" for s in cat_columns]
for col in cat_columns:
    CTsim[col] = CTsim[col].astype('category')
CTsim[cat_columns_new] = CTsim[cat_columns].apply(lambda x: x.cat.codes)

In [23]:
CTsim.dtypes

Unnamed: 0                                      int64
Unnamed: 0.1                                    int64
enrollment                                    float64
eligibility.gender                           category
eligibility.healthy_volunteers               category
eligibility.sampling_method                  category
has_expanded_access.text                     category
Minimum_age                                   float64
Maximum_age                                   float64
overall_status.text                          category
phase.text                                   category
study_design_info.allocation                 category
study_design_info.intervention_model         category
study_design_info.masking                    category
study_design_info.observational_model        category
study_design_info.primary_purpose            category
study_type.text                              category
number_of_arms                                float64
number_of_groups            

In [24]:
corr_colums = CTsim.select_dtypes(["int8",'float64']).columns
corr_colums
#CTsim[CTsim.columns[1:]].corr()['enrollment']
corr_enrollment=CTsim[corr_colums].corr()['enrollment']
corr_duration=CTsim[corr_colums].corr()['Duration_days']
corr_duration

enrollment                                   0.052663
Minimum_age                                 -0.019396
Maximum_age                                  0.035362
number_of_arms                              -0.095910
number_of_groups                            -0.016510
Target_duration                              0.085052
eligibility.gender_cat                      -0.022284
eligibility.healthy_volunteers_cat           0.120934
eligibility.sampling_method_cat              0.082690
has_expanded_access.text_cat                 0.013258
overall_status.text_cat                     -0.015296
phase.text_cat                              -0.007157
study_design_info.allocation_cat            -0.128720
study_design_info.intervention_model_cat    -0.031087
study_design_info.masking_cat               -0.079110
study_design_info.observational_model_cat    0.103926
study_design_info.primary_purpose_cat       -0.026364
study_type.text_cat                          0.114627
Duration_days               

In [25]:
corr_enrollment.to_csv("C:\\Users\\ffitzpatrick\\Desktop\\Documents perso\\Perso\\Clinical trials - project\\2. Analysis\\Analysis extract\\CT_corr_enroll.csv")

In [26]:
corr_duration.to_csv("C:\\Users\\ffitzpatrick\\Desktop\\Documents perso\\Perso\\Clinical trials - project\\2. Analysis\\Analysis extract\\CT_corr_duration.csv")

## Time series of main categories 

In [40]:
CTsim.head()
CTsim.columns.values
CTsim.dtypes
#cat_columns

Unnamed: 0                                      int64
Unnamed: 0.1                                    int64
enrollment                                    float64
eligibility.gender                           category
eligibility.healthy_volunteers               category
eligibility.sampling_method                  category
has_expanded_access.text                     category
Minimum_age                                   float64
Maximum_age                                   float64
overall_status.text                          category
phase.text                                   category
study_design_info.allocation                 category
study_design_info.intervention_model         category
study_design_info.masking                    category
study_design_info.observational_model        category
study_design_info.primary_purpose            category
study_type.text                              category
number_of_arms                                float64
number_of_groups            

### Time series of main categories

In [271]:
CT_temp=pd.DataFrame()
for col in cat_columns:
    col_name=[col]*(len(CTsim[col].cat.categories)+1)
    CT_temp=pd.concat([CT_temp,pd.crosstab(CTsim['beg_date_year'], CTsim[col+"_cat"]).
                       rename(columns=dict(enumerate(CTsim[col].cat.categories)))], axis=1)

In [264]:
#test
for col in cat_columns:
    col_name=[col]*(len(CTsim[col].cat.categories)+1)
    CT_temp=pd.concat([CT_temp,pd.crosstab(CTsim['beg_date_year'], CTsim[col+"_cat"]).
                       rename(columns=dict(enumerate(CTsim[col].cat.categories))).
                       append(col_name,ignore_index=True)], axis=1)

In [244]:
CT_temp.to_csv("C:\\Users\\ffitzpatrick\\Desktop\\Documents perso\\Perso\\Clinical trials - project\\2. Analysis\\Analysis extract\\Time series\\CT_temp.csv")

### Average enrollment, duration, success, failures per year

In [42]:
enrol_dur_avg=CTsim[["enrollment","Duration_days",'beg_date_year']].groupby(['beg_date_year']).mean()

In [45]:
CTsim['firstreceived_results_date']=CTred['firstreceived_results_date']
enrol_dur_avg["results"]=CTsim[["firstreceived_results_date",'beg_date_year']].groupby(['beg_date_year']).count()

In [48]:
CTsim['why_stopped.text']=CTred['why_stopped.text']
enrol_dur_avg["failures"]=CTsim[["why_stopped.text",'beg_date_year']].groupby(['beg_date_year']).count()

In [49]:
enrol_dur_avg.to_csv("C:\\Users\\ffitzpatrick\\Desktop\\Documents perso\\Perso\\Clinical trials - project\\2. Analysis\\Analysis extract\\CT_enrol_dur_avg.csv")

## Phase analysis

In [47]:
CTphase=CTsim[pd.isnull(CTsim['phase.text'])]

In [57]:
CTphase

Unnamed: 0  enrollment eligibility.gender  \
0                0         NaN             Female   
1                1         NaN             Female   
2                2       112.0                All   
3                3         NaN                All   
4                4         NaN                All   
5                5         NaN             Female   
6                6         NaN                All   
8                8         NaN                All   
22              22         NaN                All   
29              29         NaN                All   
42              42         NaN                All   
50              50         NaN                All   
58              58         NaN                All   
60              60      2392.0                All   
61              61         NaN                All   
67              67         NaN                All   
129            129        16.0                All   
138            138        16.0                All   
141            141        11.0                All   
142            142        19.0                All   
143            143        22.0                All   
144            144        12.0                All   
145            145        18.0                All   
147            147        20.0                All   
148            148        11.0                All   
149            149         8.0                All   
153            153        32.0                All   
247            247         NaN                All   
250            250         NaN                All   
256            256         NaN                All   
...            ...         ...                ...   
239586      239586        40.0                All   
239587      239587        60.0                All   
239589      239589       300.0             Female   
239590      239590        40.0                All   
239592      239592        74.0                All   
239593      239593       100.0                All   
239595      239595       105.0                All   
239596      239596       120.0                All   
239597      239597        50.0                All   
239598      239598      1152.0             Female   
239599      239599        45.0             Female   
239600      239600        39.0                All   
239601      239601       240.0             Female   
239602      239602       168.0                All   
239603      239603        70.0                All   
239604      239604        50.0                All   
239605      239605   2000000.0                All   
239606      239606       200.0                All   
239607      239607        16.0                All   
239608      239608       300.0                All   
239609      239609         1.0                All   
239612      239612        86.0                All   
239613      239613        12.0               Male   
239615      239615       120.0             Female   
239616      239616       300.0                All   
239617      239617        48.0                All   
239618      239618        96.0                All   
239619      239619         8.0             Female   
239620      239620       500.0                All   
239622      239622      1000.0                All   

       eligibility.healthy_volunteers eligibility.sampling_method  \
0          Accepts Healthy Volunteers                         NaN   
1          Accepts Healthy Volunteers                         NaN   
2          Accepts Healthy Volunteers          Probability Sample   
3                                  No                         NaN   
4          Accepts Healthy Volunteers                         NaN   
5          Accepts Healthy Volunteers                         NaN   
6          Accepts Healthy Volunteers                         NaN   
8          Accepts Healthy Volunteers                         NaN   
22                                 No                         NaN   
29                             

In [49]:
overall_status_count=CTphase.loc[:,'overall_status.text'].value_counts(dropna=False).sort_values(ascending=False)
study_design_intermodel_count=CTphase.loc[:,'study_design_info.intervention_model'].value_counts(dropna=False).sort_values(ascending=False)
study_design_masking_count=CTphase.loc[:,'study_design_info.masking'].value_counts(dropna=False).sort_values(ascending=False)
study_design_purpose_count=CTphase.loc[:,'study_design_info.primary_purpose'].value_counts(dropna=False).sort_values(ascending=False)
study_design_type_count=CTphase.loc[:,'study_type.text'].value_counts(dropna=False).sort_values(ascending=False)

In [17]:
CT_keyvar_phase=pd.concat([pd.DataFrame({'overall_status Val':overall_status_count.index, 'overall_status Vol':overall_status_count.values}),
                    pd.DataFrame({'study_design_intermodel Val':study_design_intermodel_count.index, 'study_design_intermodel Vol':study_design_intermodel_count.values}),
                     pd.DataFrame({'study_design_masking Val':study_design_masking_count.index, 'study_design_masking Vol':study_design_masking_count.values}),
                     pd.DataFrame({'study_design_purpose Val':study_design_purpose_count.index, 'study_design_purpose Vol':study_design_purpose_count.values}),
                     pd.DataFrame({'study_design_type Val':study_design_type_count.index, 'study_design_type Vol':study_design_type_count.values})
                    ], axis=1)

In [13]:
CT_keyvar_phase.head()

overall_status Val  overall_status Vol study_design_intermodel Val  \
0               Completed             51740.0         Parallel Assignment   
1              Recruiting             23232.0     Single Group Assignment   
2          Unknown status             12348.0        Crossover Assignment   
3  Active, not recruiting              7644.0        Factorial Assignment   
4      Not yet recruiting              5837.0       Sequential Assignment   

   study_design_intermodel Vol  \
0                      38543.0   
1                      17405.0   
2                       6266.0   
3                       1517.0   
4                         32.0   

                            study_design_masking Val  \
0                                         Open Label   
1                   Single Blind (Outcomes Assessor)   
2                             Single Blind (Subject)   
3                                         No masking   
4  Double Blind (Subject, Caregiver, Investigator...   

   study_design_masking Vol study_design_purpose Val  \
0                     32281                Treatment   
1                      5256               Prevention   
2                      4380               Diagnostic   
3                      4182          Supportive Care   
4                      2796            Basic Science   

   study_design_purpose Vol             study_design_type Val  \
0                   31302.0                    Interventional   
1                    8624.0                     Observational   
2                    5221.0  Observational [Patient Registry]   
3                    4734.0                   Expanded Access   
4                    4465.0                               NaN   

   study_design_type Vol  
0                64938.0  
1                41809.0  
2                 2716.0  
3                  347.0  
4                    NaN

In [18]:
CT_keyvar_phase.to_csv("C:\\Users\\ffitzpatrick\\Desktop\\Documents perso\\Perso\\Clinical trials - project\\2. Analysis\\Analysis extract\\CT_keyvar_phase.csv")

In [51]:
cat_columns = CTsim.select_dtypes(['category']).columns
cat_columns=cat_columns[1:len(cat_columns)]
cat_columns

Index(['eligibility.sampling_method', 'has_expanded_access.text',
       'overall_status.text', 'phase.text', 'study_design_info.allocation',
       'study_design_info.intervention_model', 'study_design_info.masking',
       'study_design_info.observational_model',
       'study_design_info.primary_purpose', 'study_type.text'],
      dtype='object')

In [46]:
for col in cat_columns:
    CTsim[col] = CTsim[col].astype('category')

In [54]:
CT_temp=pd.DataFrame()
for col in cat_columns:
    CT_temp=pd.concat([CT_temp,pd.crosstab(CTphase['beg_date_year'], CTphase[col+"_cat"]).
                       rename(columns=dict(enumerate(CTphase[col].cat.categories)))], axis=1)

In [56]:
CT_temp.to_csv("C:\\Users\\ffitzpatrick\\Desktop\\Documents perso\\Perso\\Clinical trials - project\\2. Analysis\\Analysis extract\\Time series\\CT_temp_phase.csv")